In [ ]:
 from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!pip install transformers

In [ ]:
import numpy as np
import pandas as pd

import os

In [ ]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
import matplotlib.pyplot as plt
import torchvision
from torch.utils.data import Dataset, DataLoader
import numpy as np
import math
%matplotlib inline

In [ ]:
! git clone https://github.com/EMBEDDIA/dep2label-transformers.git

Cloning into 'dep2label-transformers'...
remote: Enumerating objects: 71, done.
remote: Counting objects: 100% (71/71), done.
remote: Compressing objects: 100% (53/53), done.
remote: Total 71 (delta 35), reused 42 (delta 17), pack-reused 0
Receiving objects: 100% (71/71), 64.05 KiB | 950.00 KiB/s, done.
Resolving deltas: 100% (35/35), done.


In [ ]:
cd dep2label-transformers/


/content/dep2label-transformers


**Encoding**

In [ ]:
!python encode_dep2labels.py --input "/content/drive/My Drive/IIIT(LTRC)/Intrachunk-Train-Dev-CONLL/Telugu/train-ssf-telugu.txt" --output "/content/drive/My Drive/1train-ssf-encoded.tsv" --encoding "arc-standard"


In [ ]:
!python encode_dep2labels.py --input "/content/drive/My Drive/IIIT(LTRC)/Intrachunk-Train-Dev-CONLL/Telugu/dev-ssf-telugu.txt" --output "/content/drive/My Drive/IIIT(LTRC)../dev-ssf-encoded.tsv" --encoding "arc-standard"


Traceback (most recent call last):
  File "/content/dep2label-transformers/encode_dep2labels.py", line 18, in <module>
    encode_labels(args.file2encode, args.output, args.enc, args.mtl)
  File "/content/dep2label-transformers/encode_dep2labels.py", line 7, in encode_labels
    l.encode(file_to_encode, output, enc, mtl)
  File "/content/dep2label-transformers/dep2label/labeling.py", line 107, in encode
    p.write_to_file(encoded_sentences, output)
  File "/content/dep2label-transformers/dep2label/postprocessing.py", line 204, in write_to_file
    output_f = open(f, "w")
FileNotFoundError: [Errno 2] No such file or directory: '/content/drive/My Drive/IIIT(LTRC)../dev-ssf-encoded.tsv'


In [ ]:
!python encode_dep2labels.py --input "/content/drive/My Drive/IIIT(LTRC)/Intrachunk-Test-CONLL/test-ssf-telugu.txt" --output "/content/drive/My Drive/IIIT(LTRC)/test-ssf-encoded.tsv" --encoding "arc-standard"


**Reading data**

In [ ]:
import os
import re
import csv

def read_and_store_data(file_path):
    dep_data = []
    current_sentence = []
    ct = 0
    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            ct+=1
            line = line.strip()
            # Split the line by spaces
            elements = line.strip().split()

            # Skip empty lines
            #if not elements:
                #continue

            try:
                # Check if the line starts with '#' (indicating the start of a new sentence)
                if (line == ""):
                    if current_sentence:
                        # Append the current sentence to the dep_data list
                        dep_data.append(current_sentence)
                        current_sentence = []
                else:
                    # Extract Tamil word and POS tag and add it to the current_sentence list
                    dep_word = elements[0].strip()
                    dep_tag = elements[2].strip()
                    #print(current_sentence)
                    current_sentence.append({"word": dep_word, "dep_tag": dep_tag})
            except:
              except_d = 0
                #print(ct,end="=>")
                #print(elements)

        # Append the last sentence if any
        if current_sentence:
            dep_data.append(current_sentence)

    return dep_data

dataset = []
file_path1 = "/content/drive/My Drive/IIIT(LTRC)/train-ssf-encoded.tsv"
train_data = read_and_store_data(file_path1)

# Printing each sentence separately
for sentence in train_data:
    sent = []
    for data in sentence:
        sent.append((data['word'],data['dep_tag']))
    dataset.append(sent)

file_path9 = "/content/drive/My Drive/IIIT(LTRC)/dev-ssf-encoded.tsv"
test_data = read_and_store_data(file_path9)

testdataset = []
# Printing each sentence separately
for sentence in test_data:
    sent = []
    for data in sentence:
        sent.append((data['word'],data['dep_tag']))
    testdataset.append(sent)

file_path2 = "/content/drive/My Drive/IIIT(LTRC)/test-ssf-encoded.tsv"
predict_data = read_and_store_data(file_path2)

predictdataset = []
# Printing each sentence separately
for sentence in predict_data:
    sent = []
    for data in sentence:
        sent.append((data['word']))
    predictdataset.append(" ".join(sent))

#print(dataset[0:2])
print(testdataset[0:2])


[[('-BOS-', '-BOS-{}-BOS-'), ('వాళ్లు', 'SH{}k1'), ('ఏమనుకొంటారు', 'SH_LA{}main'), ('?', 'SH_RA_RA{}rsym'), ('-EOS-', '-EOS-{}-EOS-')], [('-BOS-', '-BOS-{}-BOS-'), ('అయితే', 'SH{}vmod'), ('ఇది', 'SH{}k1'), ('కొంతమేరకే', 'SH{}vmod'), ('పని', 'SH_LA_LA_LA{}pof'), ('చేస్తుంది', 'SH_LA{}main'), ('.', 'SH_RA_RA{}rsym'), ('-EOS-', '-EOS-{}-EOS-')]]


In [ ]:
print(dataset[0:2])

[[('-BOS-', '-BOS-{}-BOS-'), ('వారం', 'SH{}k7t'), ('దినాలు', 'SH{}k7t'), ('పరగడుపున', 'SH{}adv'), ('మింగాలి', 'SH_LA_LA_LA{}main'), ('.', 'SH_RA_RA{}rsym'), ('-EOS-', '-EOS-{}-EOS-')], [('-BOS-', '-BOS-{}-BOS-'), ('ఈ', 'SH{}nmod__adj'), ('జబ్బు', 'SH{}k4'), ('పెద్ధవాళ్లకే', 'SH{}k4'), ('వస్తుందా', 'SH_LA_LA{}main'), ('?', 'SH_RA{}rsym'), ('-EOS-', '-EOS-{}-EOS-')]]


In [ ]:
print(predictdataset[0:5])

['-BOS- రాములు పాలు తానే పితుకుతాడు . -EOS-', '-BOS- అలాగే వేసవి కాలపు వేరుసెనగ పంట తరువాత వేసుకోవచ్చు . -EOS-', '-BOS- కాలితో నేలను గీరింది . -EOS-', '-BOS- ప్రత్యేకంగా వేడి కల్పించనవసరం లేదు . -EOS-', '-BOS- రమను చేసుకోవాలని . -EOS-']


In [ ]:
train_data

[[{'word': '-BOS-', 'dep_tag': '-BOS-{}-BOS-'},
  {'word': 'వారం', 'dep_tag': 'SH{}k7t'},
  {'word': 'దినాలు', 'dep_tag': 'SH{}k7t'},
  {'word': 'పరగడుపున', 'dep_tag': 'SH{}adv'},
  {'word': 'మింగాలి', 'dep_tag': 'SH_LA_LA_LA{}main'},
  {'word': '.', 'dep_tag': 'SH_RA_RA{}rsym'},
  {'word': '-EOS-', 'dep_tag': '-EOS-{}-EOS-'}],
 [{'word': '-BOS-', 'dep_tag': '-BOS-{}-BOS-'},
  {'word': 'ఈ', 'dep_tag': 'SH{}nmod__adj'},
  {'word': 'జబ్బు', 'dep_tag': 'SH{}k4'},
  {'word': 'పెద్ధవాళ్లకే', 'dep_tag': 'SH{}k4'},
  {'word': 'వస్తుందా', 'dep_tag': 'SH_LA_LA{}main'},
  {'word': '?', 'dep_tag': 'SH_RA{}rsym'},
  {'word': '-EOS-', 'dep_tag': '-EOS-{}-EOS-'}],
 [{'word': '-BOS-', 'dep_tag': '-BOS-{}-BOS-'},
  {'word': 'రాజులు', 'dep_tag': 'SH{}k1'},
  {'word': 'తల్లి', 'dep_tag': 'SH{}k1'},
  {'word': 'ఇంట', 'dep_tag': 'SH{}vmod'},
  {'word': 'సుఖపడలేదు', 'dep_tag': 'SH_LA_LA_LA{}main'},
  {'word': '.', 'dep_tag': 'SH_RA_RA{}rsym'},
  {'word': '-EOS-', 'dep_tag': '-EOS-{}-EOS-'}],
 [{'word': '-B

Tags Count

In [ ]:
ct_total = 0
count_L = {}
for sent in dataset:
    for tup in sent:
        if tup[1] not in count_L.keys():
            count_L[tup[1]] = 0
        count_L[tup[1]] += 1
        ct_total += 1

In [ ]:
count_L

{'-BOS-{}-BOS-': 1514,
 'SH{}k7t': 145,
 'SH{}adv': 235,
 'SH_LA_LA_LA{}main': 349,
 'SH_RA_RA{}rsym': 1284,
 '-EOS-{}-EOS-': 1514,
 'SH{}nmod__adj': 268,
 'SH{}k4': 121,
 'SH_LA_LA{}main': 651,
 'SH_RA{}rsym': 213,
 'SH{}k1': 848,
 'SH{}vmod': 200,
 'SH{}ras-k1': 7,
 'SH{}k2': 739,
 'SH{}nmod': 122,
 'SH{}k7p': 214,
 'SH_LA{}k2': 92,
 'SH_LA_LA{}vmod': 66,
 'SH_LA{}vmod': 82,
 'SH_LA{}main': 386,
 'SH{}ccof': 16,
 'SH_LA_LA{}k1': 12,
 'SH_RA{}ccof': 4,
 'SH_LA{}pof': 8,
 'SH_RA{}lwg__vaux': 28,
 'SH_LA_LA{}ccof': 13,
 'SH_LA{}ccof': 14,
 'SH_RA_RA_RA{}rsym': 21,
 'SH_LA{}k7t': 41,
 'SH{}pof__cn': 168,
 'SH{}mod': 27,
 'SH_LA_LA{}k2': 24,
 'SH_LA{}k1': 104,
 'SH{}rsym': 15,
 'SH{}main': 27,
 'SH{}pof': 192,
 'SH_RA{}k1': 2,
 'SH_LA_RA{}rt': 1,
 'SH{}k4a': 26,
 'SH{}k1u': 10,
 'SH_LA_LA{}rt': 2,
 'SH_LA{}k3': 5,
 'SH{}k7': 39,
 'SH_LA_LA_LA{}rt': 2,
 'SH_LA_LA_LA_LA{}main': 74,
 'SH_LA{}k2p': 3,
 'SH{}k*u': 2,
 'SH{}k5': 22,
 'SH_LA{}k5': 2,
 'SH_LA{}rt': 13,
 'SH_LA_LA_LA_LA_LA{}main':

In [ ]:
ct_total

10524

In [ ]:
len(dataset)

1514

**Data preparation**

In [ ]:
new_dataset = []
for sent in dataset:
    sentence = []
    tags = []
    for word, tag in sent:
        sentence.append(word)
        tags.append(tag)
    new_dataset.append([sentence,tags])
dataset = new_dataset

new_dataset = []
for sent in testdataset:
    sentence = []
    tags = []
    for word, tag in sent:
        sentence.append(word)
        tags.append(tag)
    new_dataset.append([sentence,tags])
newtestdataset = new_dataset

In [ ]:
len(dataset)

1514

In [ ]:
def find_15_percent(number):

    result = 0.20 * number
    return result

input_number = len(dataset)
result = find_15_percent(input_number)
print(f"20% of {input_number} is: {result}")
print((input_number)-(result))

20% of 1514 is: 302.8
1211.2


Data_split

In [ ]:
import random
random.shuffle(dataset)
print(len(dataset))
print(dataset[1])

1514
[['-BOS-', 'తిండి', 'వెగటు', 'కలుగుతుంది', '.', '-EOS-'], ['-BOS-{}-BOS-', 'SH{}pof', 'SH{}pof', 'SH_LA_LA{}main', 'SH_RA_RA{}rsym', '-EOS-{}-EOS-']]


In [ ]:
# print(len(dataset))
train_dataset = dataset[:1211]
dev_dataset = dataset[1211:]
#test_dataset = testdataset[1850:]
test_dataset = newtestdataset
print(len(train_dataset))
print(len(dev_dataset))
print(len(test_dataset))

1211
303
185


In [ ]:
dev_dataset

[[['-BOS-',
   'భార్యభర్తలు',
   'ఇద్దరూ',
   'మాట్లాడుకొని',
   'నిర్ణయం',
   'తీసుకోవాలి',
   '.',
   '-EOS-'],
  ['-BOS-{}-BOS-',
   'SH{}k1s',
   'SH{}k1s',
   'SH_LA_LA{}vmod',
   'SH{}k2',
   'SH_LA_LA{}main',
   'SH_RA_RA{}rsym',
   '-EOS-{}-EOS-']],
 [['-BOS-',
   'గర్భవతి',
   'ఆపరేషను',
   'అయినప్పుడూ',
   ',',
   'చేయించుకోవాలసినప్పుడేనా',
   'వాళ్లకు',
   'డాక్టర్లు',
   'అవసరమయ్యేది',
   '?',
   '-EOS-'],
  ['-BOS-{}-BOS-',
   'SH{}k2',
   'SH{}k2',
   'SH{}vmod',
   'SH_RA{}rsym',
   'SH{}vmod',
   'SH{}k1',
   'SH{}k2',
   'SH_LA_LA_LA_LA{}main',
   'SH_RA{}rsym',
   '-EOS-{}-EOS-']],
 [['-BOS-', 'అని', 'వెంకటిని', 'బడికి', 'పంపింది', '.', '-EOS-'],
  ['-BOS-{}-BOS-',
   'SH{}vmod',
   'SH{}k2',
   'SH{}k2p',
   'SH_LA_LA_LA{}main',
   'SH_RA_RA{}rsym',
   '-EOS-{}-EOS-']],
 [['-BOS-', 'పాలు', 'రోజూ', 'ఒకే', 'సమయంలో', 'పిండాలి', '.', '-EOS-'],
  ['-BOS-{}-BOS-',
   'SH{}k7t',
   'SH{}k7t',
   'SH{}nmod__adj',
   'SH_LA{}k7t',
   'SH_LA_LA_LA{}main',
   'SH_RA_RA{}rsym',


**Forming Vocab, word2idx, idx2word, tag2idx, idx2tag**

In [ ]:
from tqdm import tqdm
vocab = []
tag_vocab = []
word2idx = {}
idx2word = {}
tag2idx = {}
idx2tag = {}

for sent in tqdm(dataset):
    for word in sent[0]:
        if word not in vocab:
            word2idx[word] = len(word2idx)
            idx2word[len(idx2word)] = word
            vocab.append(word)

for sent in tqdm(dataset):
    for tag in sent[1]:
        if tag not in tag_vocab:
            tag2idx[tag] = len(tag2idx)
            idx2tag[len(idx2tag)] = tag
            tag_vocab.append(tag)

print(tag_vocab)

100%|██████████| 1514/1514 [00:00<00:00, 116931.08it/s]

['-BOS-{}-BOS-', 'SH{}nmod__adj', 'SH{}ccof', 'SH_LA{}ccof', 'SH_LA_LA{}r6', 'SH_LA_RA{}ccof', 'SH{}k7', 'SH{}k7p', 'SH_LA_LA{}main', 'SH_RA{}rsym', '-EOS-{}-EOS-', 'SH{}pof', 'SH_RA_RA{}rsym', 'SH{}k7t', 'SH{}vmod', 'SH_LA_LA_LA{}main', 'SH{}adv', 'SH_LA_LA_LA_LA{}main', 'SH{}k1', 'SH_LA{}main', 'SH{}rsym', 'SH{}k2', 'SH_LA{}k1', 'SH{}mod', 'SH{}k1s', 'SH{}jk1', 'SH_LA_LA{}vmod', 'SH_LA_LA_LA{}vmod', 'SH{}nmod', 'SH{}vmod-neg', 'SH{}k4', 'SH_LA{}k2', 'SH_LA{}pof', 'SH{}pof__cn', 'SH{}main', 'SH_LA_LA{}k2', 'SH_RA_RA_RA{}rsym', 'SH_RA{}lwg__vaux', 'SH_LA{}vmod', 'SH_LA_LA{}rh', 'SH{}k5', 'SH_LA{}nmod', 'SH{}k2g', 'SH_LA{}k7t', 'SH_RA{}main', 'SH{}r6', 'SH{}rh', 'SH_LA{}r6', 'SH_LA{}k5', 'SH_LA{}k7p', 'SH_LA{}k4a', 'SH_LA{}adv', 'SH{}k1u', 'SH{}sent-adv', 'SH{}jjmod', 'SH_LA_LA{}nmod', 'SH{}k2p', 'SH{}rd', 'SH{}nmod__relc', 'SH_RA{}adv', 'SH_LA_LA_LA_LA_LA{}main', 'SH_LA_LA_LA{}rt', 'SH_LA_LA_LA{}k2', 'SH{}rbmod', 'SH{}k4a', 'SH_LA{}k3', 'SH_LA{}k1s', 'SH{}rt', 'SH_LA{}k4', 'SH_LA{}rt',

In [ ]:
word2idx

{'-BOS-': 0,
 'ఈ': 1,
 'ఏడు': 2,
 'ధర్మస్థలాలు': 3,
 'నగరాలు': 4,
 'లేదా': 5,
 'పట్టణాల': 6,
 'రూపంలో': 7,
 'గ్రంథాలలో': 8,
 'వర్ణించబడ్డాయి': 9,
 '.': 10,
 '-EOS-': 11,
 'తిండి': 12,
 'వెగటు': 13,
 'కలుగుతుంది': 14,
 'కోడిగుడ్లు': 15,
 'అప్పుడప్పుడు': 16,
 'కొద్దిగా': 17,
 'చిట్లవచ్చు': 18,
 'మన': 19,
 'దేశంలోనూ': 20,
 'కేరళలో': 21,
 'ఇట్లా': 22,
 'జరగడం': 23,
 'ఇన్స్పెక్టరుగారు': 24,
 'వెళ్ళిపోయినారు': 25,
 '"': 26,
 'డబ్బుకి': 27,
 'రశీదు': 28,
 'వచ్చింది': 29,
 'పొలంల': 30,
 'దిగడు': 31,
 'దేవాలయం': 32,
 'ప్రాంగణంలో': 33,
 'ఇంత': 34,
 'స్థలం': 35,
 'ఉంది': 36,
 'తులసి': 37,
 'తల': 38,
 'లేదని': 39,
 'అడ్డంగా': 40,
 'ఊపింది': 41,
 'చిన్న': 42,
 'దవాఖానా': 43,
 'ఒకటి': 44,
 'శంకరం': 45,
 'రమణ': 46,
 'చెప్పినదంతా': 47,
 'విన్నాడు': 48,
 'చెట్టు': 49,
 'మొదట': 50,
 'తడి': 51,
 'ఆరకుండా': 52,
 'చూచుకోవాలి': 53,
 'అవసరం': 54,
 'మార్గం': 55,
 'లేనపుడు': 56,
 'కాకుండేందుకు': 57,
 'ఏదో': 58,
 'ఆమెకు': 59,
 'తెలిసిఉండాలి': 60,
 'రంగడు': 61,
 'తన': 62,
 'ఊరు': 63,
 'చేసేది': 64,
 'చేరాడు': 65

In [ ]:
print(len(vocab))

3223


In [ ]:
print(f"Vocab size: {len(vocab)}")
print(f"word2idx size: {len(word2idx)}")
print(f"idx2word size: {len(idx2word)}")
print(f"tag2idx size: {len(tag2idx)}")
print(f"idx2tag size: {len(idx2tag)}")
print(vocab[1:10])

Vocab size: 3223
word2idx size: 3223
idx2word size: 3223
tag2idx size: 136
idx2tag size: 136
['ఈ', 'ఏడు', 'ధర్మస్థలాలు', 'నగరాలు', 'లేదా', 'పట్టణాల', 'రూపంలో', 'గ్రంథాలలో', 'వర్ణించబడ్డాయి']


In [ ]:
word2idx["X"] = len(word2idx)
idx2word[len(idx2word)] = "X"

word2idx["PAD"] = len(word2idx)
idx2word[len(idx2word)] = "PAD"

In [ ]:
print(f"Vocab size: {len(vocab)}")
print(f"word2idx size: {len(word2idx)}")
print(f"idx2word size: {len(idx2word)}")
print(f"tag2idx size: {len(tag2idx)}")
print(f"idx2tag size: {len(idx2tag)}")

Vocab size: 3223
word2idx size: 3225
idx2word size: 3225
tag2idx size: 136
idx2tag size: 136


In [ ]:
print(tag2idx.keys())

dict_keys(['-BOS-{}-BOS-', 'SH{}nmod__adj', 'SH{}ccof', 'SH_LA{}ccof', 'SH_LA_LA{}r6', 'SH_LA_RA{}ccof', 'SH{}k7', 'SH{}k7p', 'SH_LA_LA{}main', 'SH_RA{}rsym', '-EOS-{}-EOS-', 'SH{}pof', 'SH_RA_RA{}rsym', 'SH{}k7t', 'SH{}vmod', 'SH_LA_LA_LA{}main', 'SH{}adv', 'SH_LA_LA_LA_LA{}main', 'SH{}k1', 'SH_LA{}main', 'SH{}rsym', 'SH{}k2', 'SH_LA{}k1', 'SH{}mod', 'SH{}k1s', 'SH{}jk1', 'SH_LA_LA{}vmod', 'SH_LA_LA_LA{}vmod', 'SH{}nmod', 'SH{}vmod-neg', 'SH{}k4', 'SH_LA{}k2', 'SH_LA{}pof', 'SH{}pof__cn', 'SH{}main', 'SH_LA_LA{}k2', 'SH_RA_RA_RA{}rsym', 'SH_RA{}lwg__vaux', 'SH_LA{}vmod', 'SH_LA_LA{}rh', 'SH{}k5', 'SH_LA{}nmod', 'SH{}k2g', 'SH_LA{}k7t', 'SH_RA{}main', 'SH{}r6', 'SH{}rh', 'SH_LA{}r6', 'SH_LA{}k5', 'SH_LA{}k7p', 'SH_LA{}k4a', 'SH_LA{}adv', 'SH{}k1u', 'SH{}sent-adv', 'SH{}jjmod', 'SH_LA_LA{}nmod', 'SH{}k2p', 'SH{}rd', 'SH{}nmod__relc', 'SH_RA{}adv', 'SH_LA_LA_LA_LA_LA{}main', 'SH_LA_LA_LA{}rt', 'SH_LA_LA_LA{}k2', 'SH{}rbmod', 'SH{}k4a', 'SH_LA{}k3', 'SH_LA{}k1s', 'SH{}rt', 'SH_LA{}k4', 'S

In [ ]:
import numpy as np

def texts_to_sequences(text, word_index):
    sequence = []
    for token in text:
        if token in word_index.keys():
            sequence.append(word_index[token])
        else:
            sequence.append(word_index['X'])
    sequence = np.array(sequence)
    return torch.from_numpy(sequence)

Importing Tokenizer (muril - HuggingFace)

In [ ]:
from transformers import BertTokenizer

# Load the BERT tokenizer
model_name = "monsoon-nlp/muril-adapted-local"
tokenizer = BertTokenizer.from_pretrained(model_name)


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/181 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/3.16M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/113 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/411 [00:00<?, ?B/s]

In [ ]:
# Get the model's vocabulary
model_vocab = tokenizer.get_vocab()
#print(model_vocab)

Initializing the Embedding Layer

In [ ]:
EMBEDDING_SIZE = 300
VOCABULARY_SIZE = len(model_vocab)

# embedding_weights = np.zeros((VOCABULARY_SIZE, EMBEDDING_SIZE))
embedding_weights = np.random.uniform(-0.05, 0.05, size=(VOCABULARY_SIZE, EMBEDDING_SIZE))


In [ ]:
embedding_weights = torch.from_numpy(embedding_weights)

Defining the Model

In [ ]:
class BiLSTMTagger(nn.Module):

    def __init__(self, embedding_dim, hidden_dim, vocab_size, tagset_size, pretrained_embeddings, dropout = 0.3):
        ''' Initialize the layers of this model.'''
        super(BiLSTMTagger, self).__init__()

        self.hidden_dim = hidden_dim

        # embedding layer that turns words into a vector of a specified size
        self.word_embeddings = nn.Embedding(vocab_size, embedding_dim)
        self.word_embeddings.weight.data.copy_(pretrained_embeddings)
        # the LSTM takes embedded word vectors (of a specified size) as inputs
        # and outputs hidden states of size hidden_dim
        self.lstm = nn.LSTM(embedding_dim, hidden_dim, bidirectional=True)

        self.dropout = nn.Dropout(dropout)

        self.hidden2tag = nn.Linear(hidden_dim * 2, tagset_size)

        # initialize the hidden state (see code below)
        self.hidden = self.init_hidden()


    def init_hidden(self):
        ''' At the start of training, we need to initialize a hidden state;
           there will be none because the hidden state is formed based on perviously seen data.
           So, this function defines a hidden state with all zeroes and of a specified size.'''
        # The axes dimensions are (n_layers, batch_size, hidden_dim)
        return (torch.zeros(2, 1, self.hidden_dim),
                torch.zeros(2, 1, self.hidden_dim))

    def forward(self, sentence):
        ''' Define the feedforward behavior of the model.'''
        # create embedded word vectors for each word in a sentence
        embeds = self.word_embeddings(sentence)

        # get the output and hidden state by passing the lstm over our word embeddings
        # the lstm takes in our embeddings and hiddent state
        lstm_out, self.hidden = self.lstm(
            embeds.view(len(sentence), 1, -1), self.hidden)

        lstm_out = self.dropout(lstm_out)

        # get the scores for the most likely tag for a word
        tag_outputs = self.hidden2tag(lstm_out.view(len(sentence), -1))
        tag_scores = F.log_softmax(tag_outputs, dim=1)

        return tag_scores

Initializing the Model

In [ ]:
EMBEDDING_DIM = 300
HIDDEN_DIM = 128

# instantiate our model
model = BiLSTMTagger(EMBEDDING_DIM, HIDDEN_DIM, len(model_vocab), len(tag2idx), embedding_weights)

# define our loss and optimizer
loss_function = nn.NLLLoss()
optimizer = optim.Adam(model.parameters())

In [ ]:
tag_vocab
len(train_dataset)

1211

Training Loop

In [ ]:
import random
from sklearn.metrics import classification_report
from tqdm import tqdm

n_epochs = 25
batch_size = 7
accuracy = {}
accuracy_dev = {}
accuracy_test = {}
# Set device (CPU or GPU)
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model.to(device)
for epoch in range(n_epochs):
    epoch_loss = 0.0
    epoch_correct = 0
    epoch_total = 0
    print(train_dataset)
    # train_dataset = np.array(train_dataset)
    random.shuffle(train_dataset)
    mini_batches = [train_dataset[k:k+batch_size] for k in range(0, len(train_dataset), batch_size)]

    # get all sentences and corresponding tags in the training data
    for mini_batch in tqdm(mini_batches, desc="Epoch %d" % (epoch+1)):
        try:
            # print(mini_batch)
            # zero the gradients
            model.zero_grad()

            # zero the hidden state of the LSTM, this detaches it from its history
            model.hidden = model.init_hidden()

            # prepare the inputs for processing by out network,
            # turn all sentences and targets into Tensors of numerical indices
            batch_sentences = [example[0] for example in mini_batch]
            batch_tags = [example[1] for example in mini_batch]
            #print(batch_sentences)
            # calculate the loss for each sentence in the batch and accumulate the total loss
            total_loss = 0.0
            total_correct = 0
            total_total = 0
            for sentence, tags in zip(batch_sentences, batch_tags):
                sentence_in = torch.tensor(tokenizer.encode(sentence, add_special_tokens=False))
                targets = texts_to_sequences(tags, tag2idx)
    #             print(sentence_in)
    #             print(targets)
                tag_scores = model(sentence_in)
                loss = loss_function(tag_scores, targets)
                total_loss += loss
                _, predicted_tags = torch.max(tag_scores, 1)
                for i, tag in enumerate(predicted_tags):
                    if tag == targets[i]:
                        total_correct += 1
                total_total += len(targets)

            # compute the mean loss for the batch
            batch_loss = total_loss / len(mini_batch)
            epoch_loss += batch_loss.item()
            batch_correct = total_correct / total_total
            epoch_correct += batch_correct
            epoch_total += 1

            # compute gradients and update parameters
            batch_loss.backward()
            optimizer.step()
        except:
            pass
    print("Epoch: %d, loss: %1.5f, accuracy: %1.5f" % (epoch+1, epoch_loss/epoch_total, epoch_correct/epoch_total))
    epoch_correct_dev = 0
    epoch_total_dev = 0
    with torch.no_grad():
        total_loss_dev = 0.0
        total_correct_dev = 0
        total_total_dev = 0
        for sentence, tags in dev_dataset:
            sentence_in_dev = torch.tensor(tokenizer.encode(sentence, add_special_tokens=False))
            targets_dev = texts_to_sequences(tags, tag2idx)
            tag_scores_dev = model(sentence_in_dev)
            loss_dev = loss_function(tag_scores_dev, targets_dev)
            total_loss_dev += loss_dev
            _, predicted_tags_dev = torch.max(tag_scores_dev, 1)
            for i, tag in enumerate(predicted_tags_dev):
                if tag == targets_dev[i]:
                    total_correct_dev += 1
            total_total_dev += len(targets_dev)

        # compute the mean loss for the batch
        batch_correct_dev = total_correct_dev / total_total_dev
        epoch_correct_dev += batch_correct_dev
        epoch_total_dev += 1


    accuracy[epoch+1] = epoch_correct/epoch_total
    accuracy_dev[epoch+1] = epoch_correct_dev/epoch_total_dev
    print("loss: %1.5f, accuracy: %1.5f, dev_accuracy: %1.5f" % (epoch_loss/epoch_total, epoch_correct/epoch_total, epoch_correct_dev/epoch_total_dev))

[[['-BOS-', 'ఈ', 'ఏడు', 'ధర్మస్థలాలు', 'ఏడు', 'నగరాలు', 'లేదా', 'ఏడు', 'పట్టణాల', 'రూపంలో', 'గ్రంథాలలో', 'వర్ణించబడ్డాయి', '.', '-EOS-'], ['-BOS-{}-BOS-', 'SH{}nmod__adj', 'SH{}nmod__adj', 'SH{}ccof', 'SH{}nmod__adj', 'SH_LA{}ccof', 'SH_LA_LA{}r6', 'SH{}nmod__adj', 'SH_LA_RA{}ccof', 'SH{}k7', 'SH{}k7p', 'SH_LA_LA{}main', 'SH_RA{}rsym', '-EOS-{}-EOS-']], [['-BOS-', 'తిండి', 'వెగటు', 'కలుగుతుంది', '.', '-EOS-'], ['-BOS-{}-BOS-', 'SH{}pof', 'SH{}pof', 'SH_LA_LA{}main', 'SH_RA_RA{}rsym', '-EOS-{}-EOS-']], [['-BOS-', 'కోడిగుడ్లు', 'అప్పుడప్పుడు', 'కొద్దిగా', 'చిట్లవచ్చు', '.', '-EOS-'], ['-BOS-{}-BOS-', 'SH{}k7t', 'SH{}k7t', 'SH{}vmod', 'SH_LA_LA_LA{}main', 'SH_RA_RA{}rsym', '-EOS-{}-EOS-']], [['-BOS-', 'మన', 'దేశంలోనూ', 'కేరళలో', 'ఇట్లా', 'జరగడం', '.', '-EOS-'], ['-BOS-{}-BOS-', 'SH{}k7p', 'SH{}k7p', 'SH{}k7p', 'SH{}adv', 'SH_LA_LA_LA_LA{}main', 'SH_RA_RA{}rsym', '-EOS-{}-EOS-']], [['-BOS-', 'ఇన్స్పెక్టరుగారు', 'వెళ్ళిపోయినారు', '.', '-EOS-'], ['-BOS-{}-BOS-', 'SH{}k1', 'SH_LA{}main', 'SH_

Epoch 1: 100%|██████████| 173/173 [07:55<00:00,  2.75s/it]


Epoch: 1, loss: 2.52177, accuracy: 0.40273
loss: 2.52177, accuracy: 0.40273, dev_accuracy: 0.55258
[[['-BOS-', 'అత్తగారు', 'నన్ను', 'తిడుతుంది', '.', '-EOS-'], ['-BOS-{}-BOS-', 'SH{}k4', 'SH{}k4', 'SH_LA_LA{}main', 'SH_RA_RA{}rsym', '-EOS-{}-EOS-']], [['-BOS-', 'సోములు', 'దాసు', 'పోయాడు', '.', '-EOS-'], ['-BOS-{}-BOS-', 'SH{}rt', 'SH{}rt', 'SH_LA_LA{}main', 'SH_RA_RA{}rsym', '-EOS-{}-EOS-']], [['-BOS-', 'అదే', 'అడిగాడు', '.', '-EOS-'], ['-BOS-{}-BOS-', 'SH{}adv', 'SH_LA{}main', 'SH_RA_RA{}rsym', '-EOS-{}-EOS-']], [['-BOS-', 'హెక్టారుకు', '600', 'లీటర్లు', 'వాడాలి', '.', '-EOS-'], ['-BOS-{}-BOS-', 'SH{}vmod', 'SH{}nmod__adj', 'SH_LA{}vmod', 'SH_LA_LA{}main', 'SH_RA_RA{}rsym', '-EOS-{}-EOS-']], [['-BOS-', 'దానికి', 'రెండేళ్లముందు', 'పెళ్లయింది', '.', '-EOS-'], ['-BOS-{}-BOS-', 'SH{}k7t', 'SH{}k7t', 'SH_LA_LA{}main', 'SH_RA_RA{}rsym', '-EOS-{}-EOS-']], [['-BOS-', 'సీతాలు', 'దగ్గరకు', 'రాగానే', 'తీసుకున్నాడు', '.', '-EOS-'], ['-BOS-{}-BOS-', 'SH{}pof', 'SH{}pof', 'SH{}k7t', 'SH_LA_LA_LA{}m

Epoch 2: 100%|██████████| 173/173 [07:39<00:00,  2.66s/it]


Epoch: 2, loss: 1.49964, accuracy: 0.57770
loss: 1.49964, accuracy: 0.57770, dev_accuracy: 0.58795
[[['-BOS-', 'చీకటివేళ', 'గుళ్లో', 'గడపండి', '.', 'అని', 'రమ', 'అంది', '.', '-EOS-'], ['-BOS-{}-BOS-', 'SH{}k5', 'SH{}k5', 'SH_LA_LA{}ccof', 'SH_RA{}rsym', 'SH_LA{}k2', 'SH{}k1', 'SH_LA_LA{}main', 'SH_RA_RA{}rsym', '-EOS-{}-EOS-']], [['-BOS-', 'అతనితో', 'పాటు', 'భార్య', 'పొలం', 'పని', 'చేసినా', 'కుటుంబం', 'గడవటం', 'లేదు', '.', '-EOS-'], ['-BOS-{}-BOS-', 'SH{}mod', 'SH{}k1', 'SH{}k1', 'SH{}pof__cn', 'SH_LA{}k2', 'SH_LA_LA_LA{}vmod', 'SH{}k1', 'SH_LA_LA{}main', 'SH_RA{}lwg__vaux', 'SH_RA{}rsym', '-EOS-{}-EOS-']], [['-BOS-', 'తాళం', 'వేశాడు', '.', '-EOS-'], ['-BOS-{}-BOS-', 'SH{}k2', 'SH_LA{}main', 'SH_RA_RA{}rsym', '-EOS-{}-EOS-']], [['-BOS-', 'మూడు', 'నెలలకు', 'పిండం', 'చూపుడు', 'వేలంత', 'ఉంటుంది', '.', '-EOS-'], ['-BOS-{}-BOS-', 'SH{}nmod__adj', 'SH{}k1', 'SH{}k1', 'SH{}pof__cn', 'SH_LA{}k1s', 'SH_LA_LA_LA{}main', 'SH_RA{}rsym', '-EOS-{}-EOS-']], [['-BOS-', 'పొలంలో', 'నాగలి', 'మేమే', 'నడిప

...

Epoch: 23, loss: 0.39266, accuracy: 0.88890
loss: 0.39266, accuracy: 0.88890, dev_accuracy: 0.63862
[[['-BOS-', 'తులసి', 'వంతు', 'వచ్చింది', '.', '-EOS-'], ['-BOS-{}-BOS-', 'SH{}k1', 'SH{}k1', 'SH_LA_LA{}main', 'SH_RA_RA{}rsym', '-EOS-{}-EOS-']], [['-BOS-', 'సోములు', 'సంతోషించాడు', '.', '-EOS-'], ['-BOS-{}-BOS-', 'SH{}k1', 'SH_LA{}main', 'SH_RA_RA{}rsym', '-EOS-{}-EOS-']], [['-BOS-', 'గుర్రం', 'రయ్యుమని', 'దూసుకుపోయింది', '.', '-EOS-'], ['-BOS-{}-BOS-', 'SH{}k1', 'SH{}adv', 'SH_LA_LA{}main', 'SH_RA_RA{}rsym', '-EOS-{}-EOS-']], [['-BOS-', 'మా', 'నాయన', 'సంబరపడిపోతున్నాడు', '.', '-EOS-'], ['-BOS-{}-BOS-', 'SH{}k1', 'SH{}k1', 'SH_LA_LA{}main', 'SH_RA_RA{}rsym', '-EOS-{}-EOS-']], [['-BOS-', 'దీనిని', 'వారు', 'స్వీకరించారు', '.', '-EOS-'], ['-BOS-{}-BOS-', 'SH{}k1', 'SH{}k1', 'SH_LA_LA{}main', 'SH_RA_RA{}rsym', '-EOS-{}-EOS-']], [['-BOS-', 'భర్త', 'చిరునామా', 'అడిగితే', 'లాహోర్లో', 'ఉన్నాడని', 'చెపుతోంది', '.', '-EOS-'], ['-BOS-{}-BOS-', 'SH{}k2', 'SH{}k2', 'SH_LA_LA{}vmod', 'SH{}k7p', 'SH_

Epoch 24: 100%|██████████| 173/173 [07:51<00:00,  2.73s/it]


Epoch: 24, loss: 0.37075, accuracy: 0.89325
loss: 0.37075, accuracy: 0.89325, dev_accuracy: 0.63337
[[['-BOS-', 'ఇంతలో', 'చీకటి', 'పడింది', '.', '-EOS-'], ['-BOS-{}-BOS-', 'SH{}pof', 'SH{}pof', 'SH_LA_LA{}main', 'SH_RA_RA{}rsym', '-EOS-{}-EOS-']], [['-BOS-', 'ఇంత', 'నేను', 'పడేయండమ్మా', 'పోతాను', '.', '-EOS-'], ['-BOS-{}-BOS-', 'SH{}k1', 'SH{}k1', 'SH{}vmod', 'SH_LA_LA_LA{}main', 'SH_RA_RA{}rsym', '-EOS-{}-EOS-']], [['-BOS-', 'తరవాత', 'గోపాలం', 'గుడికి', 'చేరాడు', '.', '-EOS-'], ['-BOS-{}-BOS-', 'SH{}k1', 'SH{}k1', 'SH{}k2', 'SH_LA_LA_LA{}main', 'SH_RA_RA{}rsym', '-EOS-{}-EOS-']], [['-BOS-', 'నెమ్మదిగా', 'దాణాకు', 'అలవాటు', 'చేయాలి', '.', '-EOS-'], ['-BOS-{}-BOS-', 'SH{}adv', 'SH{}k4a', 'SH{}pof', 'SH_LA_LA_LA{}main', 'SH_RA_RA{}rsym', '-EOS-{}-EOS-']], [['-BOS-', 'వాటిని', 'మూట', 'కట్టాడు', 'ముగ్గులో', 'ఉంచాడు', '.', '-EOS-'], ['-BOS-{}-BOS-', 'SH{}pof', 'SH{}pof', 'SH_LA_LA{}vmod', 'SH{}k7p', 'SH_LA_LA{}main', 'SH_RA_RA{}rsym', '-EOS-{}-EOS-']], [['-BOS-', 'ఆఖరికి', 'ముఖం', 'ముడుచుకొ

Epoch 25: 100%|██████████| 173/173 [07:59<00:00,  2.77s/it]


Epoch: 25, loss: 0.35621, accuracy: 0.89655
loss: 0.35621, accuracy: 0.89655, dev_accuracy: 0.63384



Save

In [ ]:
PATH = "/content/drive/MyDrive/IIIT(LTRC)/B/BertTokenizer_Method1_50K_savedModel.pth"
torch.save(model.state_dict(),PATH)

Load

In [ ]:
PATH = "/content/drive/MyDrive/IIIT(LTRC)/B/BertTokenizer_Method1_50K_savedModel.pth"
model.load_state_dict(torch.load(PATH))

<All keys matched successfully>

In [ ]:
def predict(model, tokenizer, text):
    model.eval()
    with torch.no_grad():
        sentence_in = torch.tensor(tokenizer.encode(text, add_special_tokens=False))
        tag_scores = model(sentence_in)
        _, predicted_tags = torch.max(tag_scores, 1)


        predicted_labels = [idx2tag[tag.item()] for tag in predicted_tags]

    return predicted_labels
new_text = "అంతటితో	సుఖంగా కనేస్తుందా?"
predicted_labels = predict(model, tokenizer, new_text)
print("Predicted Labels:", predicted_labels)

Predicted Labels: ['-BOS-{}-BOS-', 'SH{}nmod', 'SH{}nmod', 'SH{}nmod', 'SH_LA{}nmod', 'SH_LA{}nmod', 'SH_RA{}ccof', 'SH_RA{}ccof', 'SH{}k1', 'SH_LA_LA_LA{}main', 'SH_RA{}rsym']


In [ ]:
epoch_correct_test = 0
epoch_total_test = 0
epoch_total = 0
model.eval()
with torch.no_grad():
    total_loss_test = 0.0
    total_correct_test = 0
    total_total_test = 0
    for sentence, tags in test_dataset:
        try:
            sentence_in_test = torch.tensor(tokenizer.encode(sentence, add_special_tokens=False))
            targets_test = texts_to_sequences(tags, tag2idx)
            tag_scores_test = model(sentence_in_test)
            loss_test = loss_function(tag_scores_test, targets_test)
            total_loss_test += loss_test
            epoch_total += 1
            _, predicted_tags_test = torch.max(tag_scores_test, 1)
            for i, tag in enumerate(predicted_tags_test):
                if tag == targets_test[i]:
                    total_correct_test += 1
            total_total_test += len(targets_test)
        except:
            pass
    batch_correct_test = total_correct_test / total_total_test
print("loss: %1.5f, test_accuracy: %1.5f" % (total_loss_test/epoch_total,total_correct_test/total_total_test ))

loss: 1.43698, test_accuracy: 0.67561


Prediction & Decoding


In [ ]:
def decode_tags(tags, idx2tag):
    return [idx2tag[tag] for tag in tags]


predicted_sentences = []
predicted_tags_list = []

epoch_correct_test = 0
epoch_total_test = 0
epoch_total = 0
model.eval()

with torch.no_grad():
    total_loss_test = 0.0
    total_correct_test = 0
    total_total_test = 0

    for sentence, tags in test_dataset:
        try:
            sentence_in_test = torch.tensor(tokenizer.encode(sentence, add_special_tokens=False))
            targets_test = texts_to_sequences(tags, tag2idx)
            tag_scores_test = model(sentence_in_test)
            loss_test = loss_function(tag_scores_test, targets_test)
            total_loss_test += loss_test
            epoch_total += 1

            _, predicted_tags_test = torch.max(tag_scores_test, 1)
            predicted_sentences.append(sentence)
            predicted_tags_list.append(predicted_tags_test.tolist())

            for i, tag in enumerate(predicted_tags_test):
                if tag == targets_test[i]:
                    total_correct_test += 1
            total_total_test += len(targets_test)
        except:
            pass

    batch_correct_test = total_correct_test / total_total_test

# Prints the predicted sentences and their corresponding tags
for sentence, predicted_tags in zip(predicted_sentences, predicted_tags_list):
    predicted_labels = decode_tags(predicted_tags, idx2tag)
    print("Sentence:", sentence)
    print("Predicted Labels:", predicted_labels)
    print()

print("loss: %1.5f, test_accuracy: %1.5f" % (total_loss_test / epoch_total, total_correct_test / total_total_test))


Sentence: ['-BOS-', 'వాళ్లు', 'ఏమనుకొంటారు', '?', '-EOS-']
Predicted Labels: ['-BOS-{}-BOS-', 'SH{}k1', 'SH_LA{}main', 'SH_RA_RA{}rsym', '-EOS-{}-EOS-']

Sentence: ['-BOS-', 'అయితే', 'ఇది', 'కొంతమేరకే', 'పని', 'చేస్తుంది', '.', '-EOS-']
Predicted Labels: ['-BOS-{}-BOS-', 'SH{}vmod', 'SH{}k2', 'SH{}nmod', 'SH_LA{}k2', 'SH_LA_LA{}main', 'SH_RA_RA{}rsym', '-EOS-{}-EOS-']

Sentence: ['-BOS-', 'నక్షత్రాలు', 'దూరంగా', 'ఉంటాయి', '.', '-EOS-']
Predicted Labels: ['-BOS-{}-BOS-', 'SH{}adv', 'SH{}adv', 'SH_LA_LA{}main', 'SH_RA_RA{}rsym', '-EOS-{}-EOS-']

Sentence: ['-BOS-', 'అంతటితో', 'సుఖంగా', 'కనేస్తుందా', '?', '-EOS-']
Predicted Labels: ['-BOS-{}-BOS-', 'SH{}k2', 'SH{}k2', 'SH_LA_LA{}main', 'SH_RA_RA{}rsym', '-EOS-{}-EOS-']

Sentence: ['-BOS-', 'దీని', 'ఆకులు', 'ఉడికించి', 'కడితే', 'వాపులు', 'తగ్గుతాయి', '.', '-EOS-']
Predicted Labels: ['-BOS-{}-BOS-', 'SH{}vmod', 'SH{}k7t', 'SH{}nmod', 'SH_LA{}nmod', 'SH{}k1', 'SH_LA_LA_LA_LA{}main', 'SH_RA_RA{}rsym', '-EOS-{}-EOS-']

Sentence: ['-BOS-', 'ఈ',

In [ ]:
df_rows = []

for sentence, predicted_tags in zip(predicted_sentences, predicted_tags_list):
    predicted_labels = decode_tags(predicted_tags, idx2tag)


    row = {'Sentence': sentence, 'Predicted Labels': predicted_labels}


    df_rows.append(row)


df_predicted = pd.DataFrame(df_rows)


df_predicted

Sentence  \
0               [-BOS-, వాళ్లు, ఏమనుకొంటారు, ?, -EOS-]   
1    [-BOS-, అయితే, ఇది, కొంతమేరకే, పని, చేస్తుంది,...   
2        [-BOS-, నక్షత్రాలు, దూరంగా, ఉంటాయి, ., -EOS-]   
3       [-BOS-, అంతటితో, సుఖంగా, కనేస్తుందా, ?, -EOS-]   
4    [-BOS-, దీని, ఆకులు, ఉడికించి, కడితే, వాపులు, ...   
..                                                 ...   
180             [-BOS-, పాడిగట్టా, అయ్యింది, ., -EOS-]   
181  [-BOS-, ఇలా, భూమి, తిరగడంలో, రాత్రి, ఏర్పడుతుం...   
182  [-BOS-, ఐరన్, మాత్రలతో, అంతాఅన్నీ, కుదుటపడవు, ...   
183         [-BOS-, అనసూయకు, సంతోషం, అయింది, ., -EOS-]   
184             [-BOS-, అని, బాధలో, అన్నారు, ., -EOS-]   

                                      Predicted Labels  
0    [-BOS-{}-BOS-, SH{}k1, SH_LA{}main, SH_RA_RA{}...  
1    [-BOS-{}-BOS-, SH{}vmod, SH{}k2, SH{}nmod, SH_...  
2    [-BOS-{}-BOS-, SH{}adv, SH{}adv, SH_LA_LA{}mai...  
3    [-BOS-{}-BOS-, SH{}k2, SH{}k2, SH_LA_LA{}main,...  
4    [-BOS-{}-BOS-, SH{}vmod, SH{}k7t, SH{}nmod, SH...  
..                                                 ...  
180  [-BOS-{}-BOS-, SH{}k1, SH_LA{}main, SH_RA_RA{}...  
181  [-BOS-{}-BOS-, SH{}vmod, SH{}r6, SH_LA{}nmod, ...  
182  [-BOS-{}-BOS-, SH{}k2, SH{}k2, SH_LA_LA{}vmod,...  
183  [-BOS-{}-BOS-, SH{}pof, SH{}k2, SH_LA_LA{}main...  
184  [-BOS-{}-BOS-, SH{}k2, SH{}k1, SH_LA_LA{}main,...  

[185 rows x 2 columns]

In [ ]:
df_rows = []

for i, (sentence, predicted_tags) in enumerate(zip(predicted_sentences, predicted_tags_list)):
    predicted_labels = decode_tags(predicted_tags, idx2tag)


    min_length = min(len(sentence), len(predicted_labels))
    for j in range(min_length):
        df_rows.append({'Sentence': sentence[j], 'Predicted Labels': predicted_labels[j]})


df_flattened = pd.DataFrame(df_rows)



print("Flattened Predicted output DataFrame saved to: predicted_output_flattened.csv")


Flattened Predicted output DataFrame saved to: predicted_output_flattened.csv


In [ ]:
df_flattened

Sentence Predicted Labels
0           -BOS-     -BOS-{}-BOS-
1          వాళ్లు           SH{}k1
2     ఏమనుకొంటారు      SH_LA{}main
3               ?   SH_RA_RA{}rsym
4           -EOS-     -EOS-{}-EOS-
...           ...              ...
1225          అని           SH{}k2
1226        బాధలో           SH{}k1
1227      అన్నారు   SH_LA_LA{}main
1228            .   SH_RA_RA{}rsym
1229        -EOS-     -EOS-{}-EOS-

[1230 rows x 2 columns]

In [ ]:

df = df_flattened

print(df)

         Sentence Predicted Labels
0           -BOS-     -BOS-{}-BOS-
1          వాళ్లు           SH{}k1
2     ఏమనుకొంటారు      SH_LA{}main
3               ?   SH_RA_RA{}rsym
4           -EOS-     -EOS-{}-EOS-
...           ...              ...
1225          అని           SH{}k2
1226        బాధలో           SH{}k1
1227      అన్నారు   SH_LA_LA{}main
1228            .   SH_RA_RA{}rsym
1229        -EOS-     -EOS-{}-EOS-

[1230 rows x 2 columns]


In [ ]:
conllx_lines = []
for idx, row in df.iterrows():
    conllx_line = f"{row['Sentence']}\t\t{row['Predicted Labels']}\n"
    conllx_lines.append(conllx_line)


output_conllx_file = "/content/drive/MyDrive/IIIT(LTRC)/B/7predicted_output.conllx"

with open(output_conllx_file, 'w', encoding='utf-8') as file:
    for line in conllx_lines:
        if line.startswith("-EOS-"):
            file.write(line + '\n')
        else:
            file.write(line)


In [ ]:
!python decode_labels2dep.py \
  --input "/content/drive/MyDrive/IIIT(LTRC)/B/7predicted_output.conllx" \
  --output "/content/drive/My Drive/IIIT(LTRC)/B/7final_output_1.conllx" \
  --encoding "arc-standard"


LAS

Making of Gold Dependecies

In [ ]:
testdataset

[[('-BOS-', '-BOS-{}-BOS-'),
  ('వాళ్లు', 'SH{}k1'),
  ('ఏమనుకొంటారు', 'SH_LA{}main'),
  ('?', 'SH_RA_RA{}rsym'),
  ('-EOS-', '-EOS-{}-EOS-')],
 [('-BOS-', '-BOS-{}-BOS-'),
  ('అయితే', 'SH{}vmod'),
  ('ఇది', 'SH{}k1'),
  ('కొంతమేరకే', 'SH{}vmod'),
  ('పని', 'SH_LA_LA_LA{}pof'),
  ('చేస్తుంది', 'SH_LA{}main'),
  ('.', 'SH_RA_RA{}rsym'),
  ('-EOS-', '-EOS-{}-EOS-')],
 [('-BOS-', '-BOS-{}-BOS-'),
  ('నక్షత్రాలు', 'SH{}k1'),
  ('దూరంగా', 'SH{}adv'),
  ('ఉంటాయి', 'SH_LA_LA{}main'),
  ('.', 'SH_RA_RA{}rsym'),
  ('-EOS-', '-EOS-{}-EOS-')],
 [('-BOS-', '-BOS-{}-BOS-'),
  ('అంతటితో', 'SH{}rh'),
  ('సుఖంగా', 'SH{}adv'),
  ('కనేస్తుందా', 'SH_LA_LA{}main'),
  ('?', 'SH_RA_RA{}rsym'),
  ('-EOS-', '-EOS-{}-EOS-')],
 [('-BOS-', '-BOS-{}-BOS-'),
  ('దీని', 'SH{}k2'),
  ('ఆకులు', 'SH{}k2'),
  ('ఉడికించి', 'SH_LA_LA{}vmod'),
  ('కడితే', 'SH_LA{}rh'),
  ('వాపులు', 'SH{}k1'),
  ('తగ్గుతాయి', 'SH_LA_LA{}main'),
  ('.', 'SH_RA_RA{}rsym'),
  ('-EOS-', '-EOS-{}-EOS-')],
 [('-BOS-', '-BOS-{}-BOS-'),
  ('ఈ', 'S

In [ ]:
flattened_data = [item for sublist in testdataset for item in sublist]

df = pd.DataFrame(flattened_data, columns=['Word', 'Label'])

print(df)


             Word           Label
0           -BOS-    -BOS-{}-BOS-
1          వాళ్లు          SH{}k1
2     ఏమనుకొంటారు     SH_LA{}main
3               ?  SH_RA_RA{}rsym
4           -EOS-    -EOS-{}-EOS-
...           ...             ...
1225          అని          SH{}k2
1226        బాధలో          SH{}k7
1227      అన్నారు  SH_LA_LA{}main
1228            .  SH_RA_RA{}rsym
1229        -EOS-    -EOS-{}-EOS-

[1230 rows x 2 columns]


In [ ]:
df

Word           Label
0           -BOS-    -BOS-{}-BOS-
1          వాళ్లు          SH{}k1
2     ఏమనుకొంటారు     SH_LA{}main
3               ?  SH_RA_RA{}rsym
4           -EOS-    -EOS-{}-EOS-
...           ...             ...
1225          అని          SH{}k2
1226        బాధలో          SH{}k7
1227      అన్నారు  SH_LA_LA{}main
1228            .  SH_RA_RA{}rsym
1229        -EOS-    -EOS-{}-EOS-

[1230 rows x 2 columns]

In [ ]:
conllx_lines = []
for idx, row in df.iterrows():
    conllx_line = f"{row['Word']}\t\t{row['Label']}\n"
    conllx_lines.append(conllx_line)


output_conllx_file = "/content/drive/MyDrive/IIIT(LTRC)/B/encoded_output.conllx"

with open(output_conllx_file, 'w', encoding='utf-8') as file:
    for line in conllx_lines:
        if line.startswith("-EOS-"):
            file.write(line + '\n')
        else:
            file.write(line)


In [ ]:
!python decode_labels2dep.py \
  --input "/content/drive/MyDrive/IIIT(LTRC)/B/encoded_output.conllx" \
  --output "/content/drive/My Drive/IIIT(LTRC)/B/5final_output_1.conllx" \
  --encoding "arc-standard"


RUn

In [ ]:



file_path =  "/content/drive/My Drive/IIIT(LTRC)/B/5final_output_1.conllx"


try:
    data2 = pd.read_csv(file_path, sep='\t', header=None, comment='#', error_bad_lines=False, quoting=3, skip_blank_lines=False, keep_default_na=False)
    print(data2.head())
except pd.errors.ParserError as e:
    print(f"Error reading the file: {e}")


   0            1  2 3  4  5  6     7  8  9
0  1       వాళ్లు  _    _  _  2    k1  _  _
1  2  ఏమనుకొంటారు  _    _  _  0  main  _  _
2  3            ?  _    _  _  2  rsym  _  _
3                                          
4  1        అయితే  _    _  _  4  vmod  _  _


<ipython-input-57-eb720dbd7561>:5: FutureWarning: The error_bad_lines argument has been deprecated and will be removed in a future version. Use on_bad_lines in the future.


  data2 = pd.read_csv(file_path, sep='\t', header=None, comment='#', error_bad_lines=False, quoting=3, skip_blank_lines=False, keep_default_na=False)


In [ ]:
data2

0            1  2 3   4  5  6     7  8  9
0     1       వాళ్లు  _     _  _  2    k1  _  _
1     2  ఏమనుకొంటారు  _     _  _  0  main  _  _
2     3            ?  _     _  _  2  rsym  _  _
3                                              
4     1        అయితే  _     _  _  4  vmod  _  _
...  ..          ... .. .. .. .. ..   ... .. ..
1040  1          అని  _     _  _  3    k2  _  _
1041  2        బాధలో  _     _  _  3    k7  _  _
1042  3      అన్నారు  _     _  _  0  main  _  _
1043  4            .  _     _  _  3  rsym  _  _
1044                                           

[1045 rows x 10 columns]

In [ ]:
words2 = data2[6].tolist()
labels2= data2[7].tolist()


In [ ]:
df2 = pd.DataFrame({'words': words2, 'labels': labels2})
df2

words labels
0        2     k1
1        0   main
2        2   rsym
3                
4        4   vmod
...    ...    ...
1040     3     k2
1041     3     k7
1042     0   main
1043     3   rsym
1044             

[1045 rows x 2 columns]

In [ ]:
df2 = pd.DataFrame({'words': words2, 'labels': labels2})

gold_dependencies_list = []
temp_dependency = []

for word, label in zip(df2['words'], df2['labels']):
    if label:

        word = int(word)
        temp_dependency.append((word, label))
    else:
        if temp_dependency:
            gold_dependencies_list.append(temp_dependency)
            temp_dependency = []


if temp_dependency:
    gold_dependencies_list.append(temp_dependency)

print(gold_dependencies_list)


[[(2, 'k1'), (0, 'main'), (2, 'rsym')], [(4, 'vmod'), (4, 'k1'), (4, 'vmod'), (5, 'pof'), (0, 'main'), (5, 'rsym')], [(3, 'k1'), (3, 'adv'), (0, 'main'), (3, 'rsym')], [(3, 'rh'), (3, 'adv'), (0, 'main'), (3, 'rsym')], [(3, 'k2'), (3, 'k2'), (4, 'vmod'), (6, 'rh'), (6, 'k1'), (0, 'main'), (6, 'rsym')], [(2, 'nmod__adj'), (4, 'k2'), (4, 'vmod'), (0, 'main'), (4, 'rsym')], [(4, 'k1'), (4, 'k1'), (4, 'adv'), (0, 'main'), (4, 'rsym')], [(0, 'root'), (1, 'r6'), (5, 'k7p'), (5, 'k2'), (1, 'main'), (5, 'rsym')], [(2, 'adv'), (5, 'k7'), (4, 'nmod__adj'), (5, 'k2'), (0, 'main'), (5, 'rsym')], [(0, 'main'), (1, 'ccof'), (2, 'rsym')], [(2, 'k7t'), (0, 'main'), (2, 'rsym')], [(0, 'main'), (1, 'rsym')], [(0, 'main'), (3, 'k1'), (1, 'ccof'), (3, 'rsym')], [(2, 'nmod__adj'), (3, 'k1'), (4, 'k1'), (0, 'main'), (4, 'rsym')], [(4, 'k4'), (4, 'k4'), (4, 'k1'), (0, 'main'), (4, 'rsym')], [(3, 'k2'), (3, 'k2'), (0, 'main'), (3, 'rsym')], [(3, 'k1'), (3, 'k1'), (0, 'main'), (3, 'rsym')], [(4, 'vmod'), (3, '

**Making a list of predicted_dependencies**

In [ ]:

file_path =  "/content/drive/My Drive/IIIT(LTRC)/B/7final_output_1.conllx"


try:
    data3 = pd.read_csv(file_path, sep='\t', header=None, comment='#', error_bad_lines=False, quoting=3, skip_blank_lines=False, keep_default_na=False)
    print(data3.head())
except pd.errors.ParserError as e:
    print(f"Error reading the file: {e}")


   0            1  2 3  4  5  6     7  8  9
0  1       వాళ్లు  _    _  _  2    k1  _  _
1  2  ఏమనుకొంటారు  _    _  _  0  main  _  _
2  3            ?  _    _  _  2  rsym  _  _
3                                          
4  1        అయితే  _    _  _  0  root  _  _


<ipython-input-65-f56a58b740ba>:5: FutureWarning: The error_bad_lines argument has been deprecated and will be removed in a future version. Use on_bad_lines in the future.


  data3 = pd.read_csv(file_path, sep='\t', header=None, comment='#', error_bad_lines=False, quoting=3, skip_blank_lines=False, keep_default_na=False)


In [ ]:
data3

0            1  2 3   4  5  6     7  8  9
0     1       వాళ్లు  _     _  _  2    k1  _  _
1     2  ఏమనుకొంటారు  _     _  _  0  main  _  _
2     3            ?  _     _  _  2  rsym  _  _
3                                              
4     1        అయితే  _     _  _  0  root  _  _
...  ..          ... .. .. .. .. ..   ... .. ..
1040  1          అని  _     _  _  3    k2  _  _
1041  2        బాధలో  _     _  _  3    k1  _  _
1042  3      అన్నారు  _     _  _  0  main  _  _
1043  4            .  _     _  _  3  rsym  _  _
1044                                           

[1045 rows x 10 columns]

In [ ]:
words3 = data3[6].tolist()
labels3= data3[7].tolist()


In [ ]:
df3 = pd.DataFrame({'words': words3, 'labels': labels3})
df3

words labels
0        2     k1
1        0   main
2        2   rsym
3                
4        0   root
...    ...    ...
1040     3     k2
1041     3     k1
1042     0   main
1043     3   rsym
1044             

[1045 rows x 2 columns]

In [ ]:
df3 = pd.DataFrame({'words': words3, 'labels': labels3})
predicted_dependencies = []
temp_dependency = []

for word, label in zip(df3['words'], df3['labels']):
    if label:
        word = int(word)
        temp_dependency.append((word, label))
    else:
        if temp_dependency:
            predicted_dependencies.append(temp_dependency)
            temp_dependency = []


if temp_dependency:
    predicted_dependencies.append(temp_dependency)

print(predicted_dependencies)


[[(2, 'k1'), (0, 'main'), (2, 'rsym')], [(0, 'root'), (5, 'k2'), (4, 'nmod'), (5, 'k2'), (1, 'main'), (5, 'rsym')], [(3, 'adv'), (3, 'adv'), (0, 'main'), (3, 'rsym')], [(3, 'k2'), (3, 'k2'), (0, 'main'), (3, 'rsym')], [(6, 'vmod'), (6, 'k7t'), (4, 'nmod'), (6, 'nmod'), (6, 'k1'), (0, 'main'), (6, 'rsym')], [(0, 'root'), (4, 'k1'), (4, 'k1'), (1, 'main'), (4, 'rsym')], [(4, 'k1'), (4, 'k1'), (4, 'adv'), (0, 'main'), (4, 'rsym')], [(0, 'root'), (5, 'r6'), (5, 'k1'), (5, 'pof'), (1, 'main'), (5, 'rsym')], [(0, 'root'), (5, 'k2'), (4, 'nmod__adj'), (5, 'k2'), (1, 'main'), (5, 'rsym')], [(2, 'k2'), (0, 'main'), (2, 'rsym')], [(2, 'k2'), (0, 'main'), (2, 'rsym')], [(0, 'main'), (1, 'rsym')], [(3, 'rh'), (3, 'k1'), (0, 'main'), (3, 'rsym')], [(0, 'root'), (4, 'k2'), (4, 'pof'), (1, 'main'), (4, 'rsym')], [(4, 'k1'), (4, 'k1'), (4, 'pof'), (0, 'main'), (4, 'rsym')], [(3, 'vmod'), (3, 'k2'), (0, 'main'), (3, 'rsym')], [(3, 'k1'), (3, 'k1'), (0, 'main'), (3, 'rsym')], [(4, 'sent-adv'), (4, 'k7p'

In [ ]:
len(gold_dependencies_list)

185

In [ ]:
len(predicted_dependencies)

185

LAS


In [ ]:
def calculate_las(gold_dependencies_list, predicted_dependencies):
    total_words = 0
    correct_attachments = 0

    for gold_sentence, predicted_sentence in zip(gold_dependencies_list, predicted_dependencies):
        total_words += len(gold_sentence)
        correct_attachments += sum((gold == predicted) for gold, predicted in zip(gold_sentence, predicted_sentence))

    las = (correct_attachments / total_words) * 100
    return las



las_score = calculate_las(gold_dependencies_list, predicted_dependencies)
print(f"Labeled Attachment Score (LAS): {las_score:.2f}%")


Labeled Attachment Score (LAS): 55.00%


UAS

In [ ]:
def calculate_uas(gold_dependencies, predicted_dependencies):
    total_words = 0
    correct_heads = 0

    for gold_sentence, predicted_sentence in zip(gold_dependencies, predicted_dependencies):
        total_words += len(gold_sentence)
        correct_heads += sum((gold_head == predicted_head) for (gold_head, _), (predicted_head, _) in zip(gold_sentence, predicted_sentence))

    uas = (correct_heads / total_words) * 100
    return uas



uas_score = calculate_uas(gold_dependencies_list, predicted_dependencies)
print(f"Unlabeled Attachment Score (UAS): {uas_score:.2f}%")


Unlabeled Attachment Score (UAS): 81.05%


In [ ]:
!pwd

/content/drive/MyDrive/IIIT(LTRC)
